# Incidence of influenza-like illness in France

In [3]:
%matplotlib inline
import matplotlib.pyplot as plt
import pandas as pd
import isoweek
import os

The data on the incidence of influenza-like illness are available from the Web site of the [Réseau Sentinelles](http://www.sentiweb.fr/). We download them as a file in CSV format, in which each line corresponds to a week in the observation period. Only the complete dataset, starting in 1984 and ending with a recent week, is available for download.

In [4]:
data_url = "http://www.sentiweb.fr/datasets/incidence-PAY-3.csv"
filename="inc-3-PAY-ds2.csv"

This is the documentation of the data from [the download site](https://ns.sentiweb.fr/incidence/csv-schema-v1.json):

| Column name  | Description                                                                                                               |
|--------------|---------------------------------------------------------------------------------------------------------------------------|
| `week`       | ISO8601 Yearweek number as numeric (year times 100 + week nubmer)                                                               |
| `indicator`  | Unique identifier of the indicator, see metadata document https://www.sentiweb.fr/meta.json                               |
| `inc`        | Estimated incidence value for the time step, in the geographic level                                                      |
| `inc_low`    | Lower bound of the estimated incidence 95% Confidence Interval                                                            |
| `inc_up`     | Upper bound of the estimated incidence 95% Confidence Interval                                                            |
| `inc100`     | Estimated rate incidence per 100,000 inhabitants                                                                          |
| `inc100_low` | Lower bound of the estimated incidence 95% Confidence Interval                                                            |
| `inc100_up`  | Upper bound of the estimated rate incidence 95% Confidence Interval                                                       |
| `geo_insee`  | Identifier of the geographic area, from INSEE https://www.insee.fr                                                        |
| `geo_name`   | Geographic label of the area, corresponding to INSEE code. This label is not an id and is only provided for human reading |

The first line of the CSV file is a comment, which we ignore with `skip=1`.

#### Download the data to a local file

To ensure reproducibility, the data link and a save name for a copy of the dataset are defined above. This next block checks if the local file is already available, to avoid repeated downloads.

In [5]:
if not os.path.exists(filename):
    raw_data = pd.read_csv(data_url, skiprows=1)
    raw_data
else:
    raw_data=pd.read_csv(filename, index=False)

#### Are there missing data points? Check if there are any empty cells.

In [8]:
absent=raw_data[raw_data.isnull().any(axis=1)]
absent

week  indicator inc  inc_low  inc_up inc100  inc100_low  inc100_up  \
1883  198919          3   -      NaN     NaN      -         NaN        NaN   

     geo_insee geo_name  
1883        FR   France

Yes, week 19 of year 1989 does not have any observed values.

In [ ]:
raw_data[raw_data.isnull().any(axis=1)]

We delete this point, which does not have big consequence for our rather simple analysis.

In [9]:
data = raw_data.dropna().copy()
data

week  indicator     inc   inc_low    inc_up inc100  inc100_low  \
0     202524          3   22816   17621.0   28011.0     34        26.0   
1     202523          3   24564   19382.0   29746.0     37        29.0   
2     202522          3   18755   14333.0   23177.0     28        21.0   
3     202521          3   23760   18671.0   28849.0     35        27.0   
4     202520          3   20265   15814.0   24716.0     30        23.0   
5     202519          3   16264   12394.0   20134.0     24        18.0   
6     202518          3   18115   13975.0   22255.0     27        21.0   
7     202517          3   22150   17291.0   27009.0     33        26.0   
8     202516          3   28564   22550.0   34578.0     43        34.0   
9     202515          3   35721   29592.0   41850.0     53        44.0   
10    202514          3   37579   31232.0   43926.0     56        47.0   
11    202513          3   39673   33686.0   45660.0     59        50.0   
12    202512          3   52543   45627.0   59459.0     78        68.0   
13    202511          3   59469   52154.0   66784.0     89        78.0   
14    202510          3   60334   53048.0   67620.0     90        79.0   
15    202509          3   84531   74994.0   94068.0    126       112.0   
16    202508          3  136020  124824.0  147216.0    203       186.0   
17    202507          3  208952  195988.0  221916.0    312       293.0   
18    202506          3  273519  258159.0  288879.0    408       385.0   
19    202505          3  334395  318416.0  350374.0    499       475.0   
20    202504          3  350043  332885.0  367201.0    522       496.0   
21    202503          3  252772  238917.0  266627.0    377       356.0   
22    202502          3  257247  242991.0  271503.0    384       363.0   
23    202501          3  231549  214627.0  248471.0    345       320.0   
24    202452          3  201726  185870.0  217582.0    302       278.0   
25    202451          3  201697  187843.0  215551.0    302       281.0   
26    202450          3  136694  126369.0  147019.0    205       190.0   
27    202449          3  108487   99037.0  117937.0    163       149.0   
28    202448          3   87381   78687.0   96075.0    131       118.0   
29    202447          3   76286   67626.0   84946.0    114       101.0   
...      ...        ...     ...       ...       ...    ...         ...   
2090  198521          3   26096   19621.0   32571.0     47        35.0   
2091  198520          3   27896   20885.0   34907.0     51        38.0   
2092  198519          3   43154   32821.0   53487.0     78        59.0   
2093  198518          3   40555   29935.0   51175.0     74        55.0   
2094  198517          3   34053   24366.0   43740.0     62        44.0   
2095  198516          3   50362   36451.0   64273.0     91        66.0   
2096  198515          3   63881   45538.0   82224.0    116        83.0   
2097  198514          3  134545  114400.0  154690.0    244       207.0   
2098  198513          3  197206  176080.0  218332.0    357       319.0   
2099  198512          3  245240  223304.0  267176.0    445       405.0   
2100  198511          3  276205  252399.0  300011.0    501       458.0   
2101  198510          3  353231  326279.0  380183.0    640       591.0   
2102  198509          3  369895  341109.0  398681.0    670       618.0   
2103  198508          3  389886  359529.0  420243.0    707       652.0   
2104  198507          3  471852  432599.0  511105.0    855       784.0   
2105  198506          3  565825  518011.0  613639.0   1026       939.0   
2106  198505          3  637302  592795.0  681809.0   1155      1074.0   
2107  198504          3  424937  390794.0  459080.0    770       708.0   
2108  198503          3  213901  174689.0  253113.0    388       317.0   
2109  198502          3   97586   80949.0  114223.0    177       147.0   
2110  198501          3   85489   65918.0  105060.0    155       120.0   
2111  198452          3   84830   60602.0  109058.0    154       110.0   
2112  198451

Our dataset uses an uncommon encoding; the week number is attached
to the year number, leaving the impression of a six-digit integer.
That is how Pandas interprets it.

A second problem is that Pandas does not know about week numbers.
It needs to be given the dates of the beginning and end of the week.
We use the library `isoweek` for that.

Since the conversion is a bit lengthy, we write a small Python 
function for doing it. Then we apply it to all points in our dataset. 
The results go into a new column 'period'.

In [ ]:
def convert_week(year_and_week_int):
    year_and_week_str = str(year_and_week_int)
    year = int(year_and_week_str[:4])
    week = int(year_and_week_str[4:])
    w = isoweek.Week(year, week)
    return pd.Period(w.day(0), 'W')

data['period'] = [convert_week(yw) for yw in data['week']]

There are two more small changes to make.

First, we define the observation periods as the new index of
our dataset. That turns it into a time series, which will be
convenient later on.

Second, we sort the points chronologically.

In [ ]:
sorted_data = data.set_index('period').sort_index()

We check the consistency of the data. Between the end of a period and
the beginning of the next one, the difference should be zero, or very small.
We tolerate an error of one second.

This is OK except for one pair of consecutive periods between which
a whole week is missing.

We recognize the dates: it's the week without observations that we
have deleted earlier!

In [ ]:
periods = sorted_data.index
for p1, p2 in zip(periods[:-1], periods[1:]):
    delta = p2.to_timestamp() - p1.end_time
    if delta > pd.Timedelta('1s'):
        print(p1, p2)

A first look at the data!

In [ ]:
sorted_data['inc'].plot()

A zoom on the last few years shows more clearly that the peaks are situated in winter.

In [ ]:
sorted_data['inc'][-200:].plot()

## Study of the annual incidence

Since the peaks of the epidemic happen in winter, near the transition
between calendar years, we define the reference period for the annual
incidence from August 1st of year $N$ to August 1st of year $N+1$. We
label this period as year $N+1$ because the peak is always located in
year $N+1$. The very low incidence in summer ensures that the arbitrariness
of the choice of reference period has no impact on our conclusions.

Our task is a bit complicated by the fact that a year does not have an
integer number of weeks. Therefore we modify our reference period a bit:
instead of August 1st, we use the first day of the week containing August 1st.

A final detail: the dataset starts in October 1984, the first peak is thus
incomplete, We start the analysis with the first full peak.

In [ ]:
first_august_week = [pd.Period(pd.Timestamp(y, 8, 1), 'W')
                     for y in range(1985,
                                    sorted_data.index[-1].year)]

Starting from this list of weeks that contain August 1st, we obtain intervals of approximately one year as the periods between two adjacent weeks in this list. We compute the sums of weekly incidences for all these periods.

We also check that our periods contain between 51 and 52 weeks, as a safeguard against potential mistakes in our code.

In [ ]:
year = []
yearly_incidence = []
for week1, week2 in zip(first_august_week[:-1],
                        first_august_week[1:]):
    one_year = sorted_data['inc'][week1:week2-1]
    assert abs(len(one_year)-52) < 2
    yearly_incidence.append(one_year.sum())
    year.append(week2.year)
yearly_incidence = pd.Series(data=yearly_incidence, index=year)

And here are the annual incidences.

In [ ]:
yearly_incidence.plot(style='*')

A sorted list makes it easier to find the highest values (at the end).

In [ ]:
yearly_incidence.sort_values()

Finally, a histogram clearly shows the few very strong epidemics, which affect about 10% of the French population,
but are rare: there were three of them in the course of 35 years. The typical epidemic affects only half as many people.

In [ ]:
yearly_incidence.hist(xrot=20)